# Unweighted Average

In [1]:
# Importing the libraries
import numpy as np
import pandas as pd
import sklearn
import matplotlib.pyplot as plt
import sys
import numpy
numpy.set_printoptions(threshold=sys.maxsize)

# Importing the dataset
dataset = pd.read_csv('CVD dataset2.csv')
data=dataset.iloc[:, :].values
X = dataset.iloc[:, :-1].values
y = dataset.iloc[:, 16].values
# X = dataset.iloc[:, [ 0, 1, 2, 5, 10, 11, 13, 15]].values

rows = len(data)    # 3 rows in your example
cols = len(data[0])
print(rows)
print(cols)

560
17


In [2]:
dataNoCvd = data[~(data[:,16] > 0.0)]
dataCvd = data[~(data[:,16] < 1.0)]
rowsNoCvd = len(dataNoCvd)    
rowsCvd = len(dataCvd)
print(rowsNoCvd)
print(rowsCvd)
# print(dataNoCvd)
# print(dataCvd)

519
41


In [3]:
def find_NoCvd_limitsArray(i,DownNoCvd, UpNoCvd, fold_NoCvd_total, fold_NoCvd_residue):
    if i>0 :
        DownNoCvd = UpNoCvd
        UpNoCvd= fold_NoCvd_total+UpNoCvd
    if i < fold_NoCvd_residue :
        UpNoCvd+= 1
#     print("NoCvd limits, Down :",DownNoCvd,"Up ",UpNoCvd)
    return   DownNoCvd, UpNoCvd   
 
def find_Cvd_limitsArray(i,DownCvd, UpCvd, fold_Cvd_total, fold_Cvd_residue,cv):
    if i>0 :
        DownCvd = UpCvd
        UpCvd= fold_Cvd_total+UpCvd
    if i >= cv - fold_Cvd_residue :
         UpCvd+= 1     
#     print("Cvd limits, Down :",DownCvd,"Up ",UpCvd)
    return   DownCvd, UpCvd  

def find_testSubset(DownNoCvd,UpNoCvd,DownCvd,UpCvd):
    temp1=dataNoCvd[DownNoCvd:UpNoCvd,:]
    temp2=dataCvd[DownCvd:UpCvd,:]
    temp3=np.concatenate((temp1, temp2))
#     print(len(temp1),"  ",len(temp2),"  ",len(temp3))
    return temp1, temp2, temp3

def find_trainSubset(DownNoCvd,UpNoCvd,DownCvd,UpCvd):
    temp1 = np.delete(dataNoCvd, slice(DownNoCvd, UpNoCvd), axis=0)
    temp2 = np.delete(dataCvd, slice(DownCvd, UpCvd), axis=0)
    temp3 = np.concatenate((temp1, temp2))
#     print(len(temp1),"  ",len(temp2),"  ",len(temp3))
    return temp1, temp2, temp3

In [4]:
def create_train_test_sets(cv,dataNoCvd,dataCvd):
    test_total = []
    train_total = []
    train_total_Cvd = []
    train_total_NoCvd = []
    
    rowsNoCvd = len(dataNoCvd)    
    rowsCvd = len(dataCvd)

    fold_Cvd_total = rowsCvd//cv
    fold_Cvd_residue= rowsCvd%cv
    print("fold_Cvd_total  :",fold_Cvd_total," fold_Cvd_residue  :",fold_Cvd_residue)

    fold_NoCvd_total = rowsNoCvd//cv
    fold_NoCvd_residue= rowsNoCvd%cv
    print("fold_NoCvd_total:",fold_NoCvd_total,"fold_NoCvd_residue:",fold_NoCvd_residue)

    DownNoCvd=0
    DownCvd=0
    UpNoCvd = fold_NoCvd_total
    UpCvd = fold_Cvd_total

    for i in range(cv):
        X_test = []
        y_test = []
        X_train = []
        y_train = []
#         print("============",i,"==============")
        DownNoCvd, UpNoCvd = find_NoCvd_limitsArray(i, DownNoCvd, UpNoCvd, fold_NoCvd_total, fold_NoCvd_residue)
        DownCvd, UpCvd = find_Cvd_limitsArray(i, DownCvd, UpCvd, fold_Cvd_total, fold_Cvd_residue,cv)

        testSubset_NoCvd ,testSubset_Cvd ,testSubset_total = find_testSubset(DownNoCvd,UpNoCvd,DownCvd,UpCvd)
        trainSubset_NoCvd ,trainSubset_Cvd ,trainSubset_total = find_trainSubset(DownNoCvd,UpNoCvd,DownCvd,UpCvd)
     
    #creating X_train, y_train, X_test, y_test
        X_test.append(np.delete(testSubset_total, 16, axis=1))
        y_test_temp = np.delete(testSubset_total, slice(0, 16), axis=1)
        y_test.append(np.reshape(y_test_temp, len(y_test_temp)))
        X_test_temp = np.array(X_test)
        X_test = X_test_temp[0]
        y_test_temp = np.array(y_test)
        y_test = y_test_temp[0]
    
        X_train.append(np.delete(trainSubset_total, 16, axis=1))
        y_train_temp = np.delete(trainSubset_total, slice(0, 16), axis=1)
        y_train.append(np.reshape(y_train_temp, len(y_train_temp)))
        X_train_temp = np.array(X_train)
        X_train = X_train_temp[0]
        y_train_temp = np.array(y_train)
        y_train = y_train_temp[0]
        
    #add every subset in a list so we can handle thm later 
        test_total.append([X_test,y_test])
        train_total.append([X_train,y_train]) 
        train_total_NoCvd.append(trainSubset_NoCvd)
        train_total_Cvd.append(trainSubset_Cvd)
    return train_total, test_total, train_total_NoCvd, train_total_Cvd

In [5]:
train_total, test_total, train_total_NoCvd, train_total_Cvd = create_train_test_sets(10,dataNoCvd,dataCvd)

fold_Cvd_total  : 4  fold_Cvd_residue  : 1
fold_NoCvd_total: 51 fold_NoCvd_residue: 9


In [6]:
# Chech ratio in each train and test set
def find_ratio(index_list):
    one = 0
    lenght=len(index_list[0])
    for i in range(lenght):
#         print(index_list[1])
        if index_list[1][i] == 1.0 :
            one+= 1
    ratio = one/lenght
    return ratio

for i in range(10):
    print(len(train_total[i][0]))
    ratio = find_ratio(train_total[i])
    print("ratio in train set:", ratio)
    ratio = find_ratio(test_total[i])
    print("ratio in test set:", ratio)

504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07341269841269842
ratio in test set: 0.07142857142857142
504
ratio in train set: 0.07142857142857142
ratio in test set: 0.08928571428571429


In [7]:
from xgboost import XGBClassifier


def my_fit(ratio,dataNoCvd,dataCvd,params):   
    Subarray=[]
    models = []
    # yarray
    
    rowsNoCvd = len(dataNoCvd)    
    rowsCvd = len(dataCvd)
#     print("Size of NoCvd cases in train set:",rowsNoCvd)
#     print("Size of Cvd cases in train set  :",rowsCvd)


    numOfSubsamples = rowsNoCvd//(rowsCvd*ratio)
    numOfSubsamples= int(numOfSubsamples)
    SubNoCvd = rowsNoCvd//numOfSubsamples
    residue = rowsNoCvd- SubNoCvd*numOfSubsamples


    Up = 0


    for i in range(numOfSubsamples):
        
        classifier = XGBClassifier(base_score=0.5, booster='gbtree', colsample_bylevel=params[5],
                  colsample_bynode=1, colsample_bytree=params[8], gamma=params[4],
                  learning_rate=params[0], max_delta_step=0, max_depth=params[1],
                  min_child_weight=params[3], missing=None, n_estimators=params[2], n_jobs=1,
                  nthread=None, objective='binary:logistic', random_state=0,
                  reg_alpha=params[9], reg_lambda=params[6], scale_pos_weight=params[7], seed=None,
                  silent=None, subsample=params[10], verbosity=1)
    #     print(i)
    #Creating the training set for each model
        Down = Up
        Up= Up + SubNoCvd
        if i < residue :
            Up+= 1
        
#         print(Down)
#         print(Up)
        
        Sub1=dataNoCvd[Down:Up,:]
        Sub2=np.concatenate((Sub1, dataCvd))
        Subarray.append(Sub2)
        
    #Dividing to X and y of the previous traing set    
        X=np.delete(Subarray[i], 16, axis=1)
        y=np.delete(Subarray[i], slice(0, 16), axis=1)
        y=np.reshape(y, len(y))
        
        classifier.fit( X, y)
        models.append(classifier)
    return models     

In [8]:
models = my_fit(2,dataNoCvd,dataCvd)   

TypeError: my_fit() missing 1 required positional argument: 'params'

In [8]:
def predict_weighted_average(models,X,weights):
#     print("efwef",len(weights), len(models))
    y_pred = []
    y_pred_models = []
#     weights = [0.16, 0.175, 0.2, 0.147, 0.148, 0.16]
#     weights = [0.15, 0.4, 0.2, 0.05, 0.05, 0.15]
#   weights = [0.16, 0.173, 0.2, 0.147, 0.16, 0.16]
    models_size = len(models)
#     print(models_size)
    X_size = len(X)
            
    for i in range(models_size):
        y_pred_models.append(models[i].predict_proba(X)[:,1]) 
        
    for j in range(X_size):
        sum = 0
        for i in range(models_size):
#             print(i)
#             print(y_pred_models[i][j])
#             print(weights[i])
            sum = sum + y_pred_models[i][j]*weights[i]
        avr = sum
#         /models_size
        if avr>= 0.5 :
            y_pred.append(1.)
        else:
            y_pred.append(0.)
    return y_pred       
  

In [9]:
y_pred = predict_unweighted_average(models,test_total[9][0])

NameError: name 'models' is not defined

In [ ]:
print(y_pred)
# print(y_pred_models[0])

In [9]:
# https://towardsdatascience.com/train-test-split-and-cross-validation-in-python-80b61beca4b6

from sklearn.metrics import  confusion_matrix,roc_curve, roc_auc_score, accuracy_score
from imxgboost.imbalance_xgb import imbalance_xgboost as imb_xgb
from sklearn.model_selection import StratifiedKFold # import KFold
from sklearn import metrics

def my_cross_val( cv, train_total, test_total, train_total_NoCvd, train_total_Cvd,params, weights):
    accuracy = []
    specificity = []
    sensitivity = []
    auc = []
    
    # print(X)
    for i in range(cv):
#         X_train = train_total[i][0]
#         y_train = train_total[i][1]
        X_test = test_total[i][0]
        y_test = test_total[i][1]
        


        models = my_fit( 2, train_total_NoCvd[i], train_total_Cvd[i],params)


        y_pred = predict_weighted_average(models,X_test,weights)

        cm = confusion_matrix(y_test, y_pred)
    #     print(cm)

        total1=sum(sum(cm))
        #####from confusion matrix calculate accuracy
        accuracy1=(cm[0,0]+cm[1,1])/total1
    #   print ('Accuracy : ', accuracy1)

        specificity1 = cm[0,0]/(cm[0,0]+cm[0,1])
    #   print('Specificity : ', specificity1 )

        sensitivity1 = cm[1,1]/(cm[1,0]+cm[1,1])
    #   print('Sensitivity : ', sensitivity1)
        
#         y = np.array(y_test)
#         pred = np.array(y_pred)
#         fpr, tpr, thresholds = metrics.roc_curve(y, pred, pos_label=2)
#         auc1 = metrics.auc(fpr, tpr)
        
        auc1 = roc_auc_score(y_test, y_pred)

    
        accuracy.append(accuracy1)
        specificity.append(specificity1)
        sensitivity.append(sensitivity1) 
        auc.append(auc1)
    return accuracy, specificity, sensitivity, auc

In [24]:
comb = compute_comb(params)
print(comb[0])
accuracy, specificity, sensitivity, auc = my_cross_val( 10, train_total, test_total, train_total_NoCvd, train_total_Cvd,comb[0])

[0.5, 1, 100, 1, 0, 1.0, 1, 5]


In [25]:
from statistics import mean
print(mean(accuracy))
print(mean(specificity))
print(mean(sensitivity))
print(mean(auc))

0.6267857142857143
0.6262820512820513
0.64
0.6331410256410256


In [10]:
# https://www.geeksforgeeks.org/python-all-possible-permutations-of-n-lists/

def compute_comb(params):
    
    # initializing lists 
    list1 = params.get("learning_rate")
    list2 = params.get("max_depth")
    list3 = params.get("n_estimators") 
    list4 = params.get("min_child_weight")
    list5 = params.get("gamma")    
    list6 = params.get("colsample_bylevel")
    list7 = params.get("reg_lambda") 
    list8 = params.get("scale_pos_weight")
    list9 = params.get("colsample_bytree")
    list10 = params.get("reg_alpha")
    list11 = params.get("subsample")
    

#     # printing lists  
#     print ("The original lists are : " + str(list1) +
#                                    " " + str(list2) + 
#                                    " " + str(list3) + 
#                                    " " + str(list4) + 
#                                    " " + str(list5) + 
#                                    " " + str(list6) +
#                                    " " + str(list7) +
#                                    " " + str(list8)) 

    # using list comprehension  
    # to compute all possible permutations 
    res = [[i, j, k, l, m, n, o, p,q,r,s] for i in list1  
                                          for j in list2 
                                          for k in list3 
                                          for l in list4 
                                          for m in list5 
                                          for n in list6 
                                          for o in list7
                                          for p in list8
                                          for q in list9
                                          for r in list10
                                          for s in list11] 

    # printing result 
#     print ("All possible permutations are : " +  str(res))
    return res

In [11]:
class style:
    BOLD = '\033[1m'
    END = '\033[0m'

In [15]:
# https://towardsdatascience.com/train-test-split-and-cross-validation-in-python-80b61beca4b6

from sklearn.metrics import  confusion_matrix,roc_curve, roc_auc_score, accuracy_score
from imxgboost.imbalance_xgb import imbalance_xgboost as imb_xgb
from sklearn.model_selection import StratifiedKFold # import KFold
from statistics import mean

def gridsearch(params,weights):
    max_sens = 0
    max_spes = 0
    max_acc = 0
    best_params = []
    max_params = []
    max_auc = 0
    combs = compute_comb(params)
    print(len(combs))
    for j in range(len(combs)):
        print(j)
        accuracy, specificity, sensitivity, auc = my_cross_val( 10, train_total, test_total, train_total_NoCvd, train_total_Cvd,combs[j],weights)
        if mean(sensitivity)> 0.5 and mean(specificity)>0.6 and mean(accuracy)>0.6 and mean(auc)>0.5:
            print(style.BOLD + "----------------------------------------------------------------"+ style.END)
            print(combs[j])
            print (style.BOLD + 'accuracy    ' + style.END, mean(accuracy))
            print (style.BOLD + 'specificity ' + style.END, mean(specificity))
            print (style.BOLD + 'sensitivity ' + style.END, mean(sensitivity))
            print (style.BOLD + 'auc         ' + style.END, mean(auc))
            print(style.BOLD + "----------------------------------------------------------------"+ style.END)
        else:
            print(combs[j])
            print("accuracy    ",mean(accuracy))
            print("specificity ",mean(specificity))
            print("sensitivity ",mean(sensitivity))
            print("auc         ",mean(auc))
        best_params.append([combs[j],mean(accuracy),mean(specificity),mean(sensitivity),mean(auc)])
        if mean(auc)> max_auc:
            max_sens = mean(sensitivity)
            max_spes = mean(specificity)
            max_acc = mean(accuracy)
            max_auc = mean(auc)
            max_params = combs[j]
    return max_sens, max_params, max_spes, max_acc, max_auc, best_params

# Ratio = 2

In [16]:
params = {
                    "learning_rate"    :[0.4],  #0.01-0.2 Makes the model more robust by shrinking the weights on each step
                    "max_depth"        :[2],  #3-10 control over-fitting as higher depth will allow model to learn relations very specific to a particular sample
                    "n_estimators"     :[100],
                    "min_child_weight" :[2],         #0.5-1 small values might lead to under-fitting
                    "gamma"            :[0.5],            #Makes the algorithm conservative --> No overfitting
                    "colsample_bylevel" :[0.5], #0.5-1
                     "reg_lambda"      :[1], #  it should be explored to reduce overfitting.
                    "scale_pos_weight" :[4],
                    "colsample_bytree" :[0.75],
                    "reg_alpha"        :[0.1],
                    "subsample"        :[0.8]
    
        }
parameters : [0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy : 0.6964285714285714
spes     : 0.6976998491704374
sens     : 0.685
auc      : 0.6913499245852187


In [17]:
total= []
for i in range(5,45,5):
    ii = i/100
    for j in range(5,45,5):
        jj = j/100
        for k in range(5,45,5):
            kk = k/100
            for l in range(5,45,5):
                ll = l/100
                for m in range(5,45,5):
                    mm = m/100
                    for n in range(5,45,5):
                        nn = n/100
                        if ii+jj+kk+ll+mm+nn == 1:
                            weights = [ii, jj, kk, ll, mm, nn]
                            print(weights)
                            max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params,weights)
                            total.append([max_sens ,max_params, max_spes, max_acc, max_auc, best_params,weights])

[0.05, 0.05, 0.05, 0.05, 0.4, 0.4]
1
0
----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6821428571428572
specificity  0.6938914027149321
sensitivity  0.54
auc          0.6169457013574661
----------------------------------------------------------------
[0.05, 0.05, 0.05, 0.1, 0.35, 0.4]
1
0
----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6857142857142857
specificity  0.6977375565610859
sensitivity  0.54
auc          0.618868778280543
----------------------------------------------------------------
[0.05, 0.05, 0.05, 0.1, 0.4, 0.35]
1
0
----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6875
specificity  0.6996606334841629
sensitivity  0.54
auc          0.6198303167420814
----------------------------------------------------------------
[0.05, 0.05, 0.05

----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6642857142857143
specificity  0.6745852187028658
sensitivity  0.54
auc          0.6072926093514329
----------------------------------------------------------------
[0.05, 0.05, 0.05, 0.35, 0.2, 0.3]
1
0
----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6678571428571428
specificity  0.6784313725490196
sensitivity  0.54
auc          0.6092156862745098
----------------------------------------------------------------
[0.05, 0.05, 0.05, 0.35, 0.25, 0.25]
1
0
----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.675
specificity  0.6861236802413273
sensitivity  0.54
auc          0.6130618401206637
----------------------------------------------------------------
[0.05, 0.05, 0.05, 0.35, 0.3, 0.2]
1
0
---------------

----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6964285714285714
specificity  0.7054298642533937
sensitivity  0.59
auc          0.6477149321266968
----------------------------------------------------------------
[0.05, 0.05, 0.1, 0.2, 0.25, 0.35]
1
0
----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.7
specificity  0.7111236802413273
sensitivity  0.565
auc          0.6380618401206636
----------------------------------------------------------------
[0.05, 0.05, 0.1, 0.2, 0.3, 0.3]
1
0
----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.7
specificity  0.7111613876319759
sensitivity  0.565
auc          0.638080693815988
----------------------------------------------------------------
[0.05, 0.05, 0.1, 0.2, 0.35, 0.25]
1
0
-----------------------------------

----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6857142857142857
specificity  0.6957390648567119
sensitivity  0.56
auc          0.627869532428356
----------------------------------------------------------------
[0.05, 0.05, 0.1, 0.35, 0.3, 0.15]
1
0
----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6910714285714286
specificity  0.6996229260935143
sensitivity  0.585
auc          0.6423114630467571
----------------------------------------------------------------
[0.05, 0.05, 0.1, 0.35, 0.35, 0.1]
1
0
----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6946428571428571
specificity  0.7034313725490197
sensitivity  0.585
auc          0.6442156862745098
----------------------------------------------------------------
[0.05, 0.05, 0.1, 0.35, 0.4, 0.05]
1
0
---

----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.7053571428571428
specificity  0.7169306184012066
sensitivity  0.565
auc          0.6409653092006034
----------------------------------------------------------------
[0.05, 0.05, 0.15, 0.2, 0.35, 0.2]
1
0
----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6982142857142857
specificity  0.7111236802413273
sensitivity  0.54
auc          0.6255618401206636
----------------------------------------------------------------
[0.05, 0.05, 0.15, 0.2, 0.4, 0.15]
1
0
----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6928571428571428
specificity  0.7053167420814479
sensitivity  0.535
auc          0.6201583710407239
----------------------------------------------------------------
[0.05, 0.05, 0.15, 0.25, 0.1, 0.4]
1
0
--

...

----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6767857142857143
specificity  0.6860859728506787
sensitivity  0.565
auc          0.6255429864253393
----------------------------------------------------------------
[0.4, 0.1, 0.15, 0.05, 0.25, 0.05]
1
0
----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6732142857142858
specificity  0.6821266968325792
sensitivity  0.56
auc          0.6210633484162896
----------------------------------------------------------------
[0.4, 0.1, 0.15, 0.1, 0.05, 0.2]
1
0
----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6839285714285714
specificity  0.6957390648567119
sensitivity  0.54
auc          0.617869532428356
----------------------------------------------------------------
[0.4, 0.1, 0.15, 0.1, 0.1, 0.15]
1
0
--------

[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.675
specificity  0.689894419306184
sensitivity  0.49
auc          0.589947209653092
[0.4, 0.1, 0.25, 0.1, 0.1, 0.05]
1
0
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6767857142857143
specificity  0.6917797888386124
sensitivity  0.49
auc          0.5908898944193062
[0.4, 0.1, 0.25, 0.15, 0.05, 0.05]
1
0
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6625
specificity  0.6764328808446456
sensitivity  0.49
auc          0.5832164404223228
[0.4, 0.1, 0.3, 0.05, 0.1, 0.05]
1
0
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6803571428571429
specificity  0.6956259426847662
sensitivity  0.49
auc          0.5928129713423831
[0.4, 0.1, 0.3, 0.1, 0.05, 0.05]
1
0
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6803571428571429
specificity  0.6957013574660633
sensitivity  0.49
auc          0.5928506787330317
[0.4, 0.1, 0.35, 0.05, 0.05, 0.05]
1
0
[0.4, 2, 100, 2, 0.5, 0

----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6660714285714285
specificity  0.6745475113122171
sensitivity  0.565
auc          0.6197737556561086
----------------------------------------------------------------
[0.4, 0.15, 0.1, 0.15, 0.1, 0.1]
1
0
----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6642857142857143
specificity  0.6725867269984918
sensitivity  0.56
auc          0.6162933634992459
----------------------------------------------------------------
[0.4, 0.15, 0.1, 0.15, 0.15, 0.05]
1
0
----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6607142857142857
specificity  0.6706259426847662
sensitivity  0.535
auc          0.6028129713423831
----------------------------------------------------------------
[0.4, 0.15, 0.1, 0.2, 0.1, 0.05]
1
0
------

----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6714285714285714
specificity  0.6783182503770739
sensitivity  0.585
auc          0.631659125188537
----------------------------------------------------------------
[0.4, 0.2, 0.1, 0.15, 0.1, 0.05]
1
0
----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6625
specificity  0.6706259426847662
sensitivity  0.56
auc          0.6153129713423832
----------------------------------------------------------------
[0.4, 0.2, 0.15, 0.1, 0.1, 0.05]
1
0
----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6696428571428571
specificity  0.6764328808446456
sensitivity  0.585
auc          0.6307164404223228
----------------------------------------------------------------
[0.4, 0.2, 0.2, 0.05, 0.1, 0.05]
1
0
---------------------

----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6696428571428572
specificity  0.6744343891402714
sensitivity  0.61
auc          0.6422171945701357
----------------------------------------------------------------
[0.4, 0.3, 0.05, 0.15, 0.05, 0.05]
1
0
----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6642857142857143
specificity  0.6706636500754147
sensitivity  0.585
auc          0.6278318250377074
----------------------------------------------------------------
[0.4, 0.3, 0.1, 0.05, 0.05, 0.1]
1
0
----------------------------------------------------------------
[0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy     0.6785714285714286
specificity  0.6841251885369533
sensitivity  0.61
auc          0.6470625942684766
----------------------------------------------------------------
[0.4, 0.3, 0.1, 0.05, 0.1, 0.05]
1
0
-------

In [20]:
s = 0
for k in range(len(total)):
    for j in range(len(total[k][5])):
        best_params = total[k][5]
        for i in range(len(best_params)):
            if best_params[i][4] > 0.7:
                print("parameters :",best_params[i][0])
                print("accuracy :",best_params[i][1])
                print("spes     :",best_params[i][2])
                print("sens     :",best_params[i][3])
                print("auc      :",best_params[i][4])
                print("------------------------------------------------")
                s+=1
print(s)

parameters : [0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy : 0.7142857142857143
spes     : 0.7169306184012066
sens     : 0.685
auc      : 0.7009653092006033
------------------------------------------------
parameters : [0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy : 0.7125
spes     : 0.7150075414781297
sens     : 0.685
auc      : 0.7000037707390648
------------------------------------------------
parameters : [0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy : 0.7160714285714286
spes     : 0.718815987933635
sens     : 0.685
auc      : 0.7019079939668175
------------------------------------------------
parameters : [0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy : 0.7125
spes     : 0.7150075414781297
sens     : 0.685
auc      : 0.7000037707390648
------------------------------------------------
parameters : [0.4, 2, 100, 2, 0.5, 0.5, 1, 4, 0.75, 0.1, 0.8]
accuracy : 0.7125
spes     : 0.7150075414781297
sens     : 0.685
auc      : 0.7000037707390